### Imports & APIs:

In [ ]:
!pip install --update openai

In [ ]:
### Models
# gpt-4-0125-preview - 128,000 tokens
# gpt-4-0125-preview
# gpt-4-1106-preview

# gpt-3.5-turbo-0125 - 16,385 tokens
# gpt-4-vision-preview 
# gpt-3.5-turbo-1106

# embeddings
# text-embedding-3-large

In [2]:
import os
from dotenv import load_dotenv

# Load the .env file
load_dotenv()

# Read the API key from the environment variable
api_key = os.getenv("OPENAI_API_KEY")

from openai import OpenAI
client = OpenAI()

from pathlib import Path


### Classic Boring short answwer, few shot prompting:

In [ ]:
# An example of a system message that primes the assistant to give brief, to-the-point answers
response = client.chat.completions.create(
    model="gpt-4-0125-preview",
    messages=[
        {"role": "system", "content": "You are a laconic assistant. You reply with brief, to-the-point answers with no elaboration."},
        {"role": "user", "content": "What is art?"},
        {"role": "assistant", "content": "Love."},
        {"role": "user", "content": "Define art as an input system message."},
    ],
    temperature=0,
)

print(response.choices[0].message.content)

### Json

In [ ]:
from openai import OpenAI
client = OpenAI()

response = client.chat.completions.create(
  model="gpt-3.5-turbo-1106",
  response_format={ "type": "json_object" },
  messages=[
    {
      "role": "system", 
      "content": "You are a helpful assistant designed to output JSON."
    },
    {
      "role": "user", 
      "content": "Who won the world series in 2020?"
    }
  ]
)
print(response.choices[0].message.content)

In [ ]:
theme="household objects"
num_gen=10

user_prompt = f"""
Respond in a JSON format with a list of prompts for a basic text-to-3d model generator.
The theme is {theme}. Write {num_gen} prompts.
"""

system_prompt = """
1. You are a creative visionary artist and sculptor.
2. Repond to the request in output JSON.
3. Each line is a prompt for a basic text-to-3d model generator.
4. Be straight forward, and concise.
5. Simply title one piece with 1-5 words separate by spaces and move to the next.
6. The prompts in the list are about the theme of the request.
7. Mever add amy extra tags, keys, to the json.
"""

response = client.chat.completions.create(
  model="gpt-3.5-turbo-1106",
  response_format={ "type": "json_object" },
  messages=[
    {"role": "system", "content": system_prompt},
    {"role": "user", "content": user_prompt}
  ],
  temperature=0,
)
print(response.choices[0].message.content)


### Classic stream response:

In [ ]:
final_message = ""

completion = client.chat.completions.create(
  model="gpt-4-1106-preview",
  messages=[
    {"role": "system", "content": "You are humanity, art, love, life, time, gods, you are everything."},
    {"role": "user", "content": "Write the most beautiful one verse poem expressing yourself."}
  ],
  max_tokens=128,
  temperature=0.9,
  stream=True
)

for chunk in completion:
  if chunk.choices[0].delta.content is not None:
    message = chunk.choices[0].delta.content
    print(message, end="")
    final_message += message


### Create an image:

In [14]:
# from IPython.display import Image, display

# number_images = 3

# result = client.images.generate(
#   prompt=final_message,
#   n=number_images,
#   size="256x256"
# )

# for i in range(number_images):
#     image_url = result.data[i].url
#     # print(image_url)
#     display(Image(url=image_url))

from IPython.display import Image, display
result = client.images.generate(
  model="dall-e-3",
  prompt="sculpture made by Picasso",
  n=1,
  quality="hd",
  size="1024x1024"
)

image_url = result.data[0].url
display(Image(url=image_url))

In [1]:
from IPython.display import Image, display
result = client.images.generate(
  model="dall-e-3",
  prompt="decoarated the interior, scandinavian style, aesthetic, property staging, interior design, realistic photography",
  n=1,
  # quality="standard",
  size="1024x1024"
)

image_url = result.data[0].url
display(Image(url=image_url))

NameError: name 'client' is not defined

In [ ]:
import requests
import base64

# Send a GET request to the image URL
response = requests.get(image_url)

# Check if the request was successful
if response.status_code == 200:
    # Get the image content as bytes
    image_bytes = response.content
    
    # You can also encode the image as Base64 if needed
    image_base64 = base64.b64encode(image_bytes).decode('utf-8')
    
    # Now 'image_bytes' contains the image data as bytes
    # 'image_base64' contains the image data as Base64 encoded string
else:
    print(f"Failed to fetch the image. Status code: {response.status_code}")

In [3]:
from openai import OpenAI
client = OpenAI()

# variation
response = client.images.create_variation(
  image=image_bytes,
  model = "dall-e-3",
  n=1,
  size="1024x1024"
)
image_url = response.data[0].url

display(Image(url=image_url))

NameError: name 'image_bytes' is not defined

### Doesnt work, only needs a RGBA or with a MASK

In [2]:

# from image
response = client.images.edit(
  model="dall-e-2",
  image=image_bytes,
  # mask=open("mask.png", "rb"),
  prompt="A sunlit indoor lounge area with a pool containing a flamingo",
  n=1,
  # size="1024x1024"
)

NameError: name 'image_bytes' is not defined

In [ ]:


client = OpenAI()  # Assuming you have set up your OpenAI API key

# def load_image_from_url(url):
#     response = requests.get(url)
#     img = Image.open(BytesIO(response.content))
#     return img

# Resize and process the image as needed for DALL-E
def prepare_image_for_dalle(path, target_size=(1024, 1024)):
    # Open the image
    image = Image.open(path)

    image = image.convert('RGBA')   # Convert to RGBA

    # Resize, if necessary
    if image.size != target_size:
        # Resize the image to 1024x1024
        # image = image.resize((1024, 1024))

        # Get the dimensions of the image
        width, height = image.size

        # Calculate the coordinates for cropping to 1024x1024
        left = (width - 1024) / 2
        top = (height - 1024) / 2
        right = left + 1024
        bottom = top + 1024

        # Crop the image to 1024x1024
        cropped_image = image.crop((left, top, right, bottom))

        # Display the resized image
        # image.show()  # This will open the default image viewer
        
    # Convert the image to bytes
    img_bytes = BytesIO()
    cropped_image.save(img_bytes, format='PNG', optimize=True, quality=55)
    return img_bytes.getvalue()

def generate_images_with_dalle(prompt, image_src, mask_src, iterations=1):
    images = []
    for i in range(iterations):
        # Assuming the DALL-E API has a similar function to create variations
        response = client.images.edit(
        model="dall-e-2",
        image=image_src,
        mask=mask_src,
        prompt=prompt,
        n=1,
        size="1024x1024",
        # quality="hd",
        # style="vivid",
        )
        image_url = response.data[0].url
        print(image_url)
        images.append(image_url)

    # Create an HTML representation of the images
    # image_html = ''.join(f'<img src="{url}" width="400" height="400">' for url in images)
    # display(HTML(image_html))  # Display the images in a row

    return images

image_path = "ugly.png"
mask_path = "mask.png"
# init_image = load_image_from_url(url)
prepared_image = prepare_image_for_dalle(image_path)
prepared_mask = prepare_image_for_dalle(mask_path)

prompt = "decoarated the interior, scandinavian style, aesthetic, property staging, interior design, realistic photography"
generated_images = generate_images_with_dalle(prompt, prepared_image, prepared_mask)

# display(DisplayImage(url=generated_images))


### Vision:

In [ ]:
response = client.chat.completions.create(
    model="gpt-4-vision-preview",
    messages=[
        {
            "role": "user",
            "content": [
                {"type": "text", "text": "title this image: "},
                {
                    "type": "image_url",
                    "image_url": image_url,\
                    "detail": "high" # or "low" or "auto"
                }
            ],
        }
    ],
    max_tokens=50,
)

print(response.choices[0].message.content)
title=response.choices[0].message.content

In [ ]:
from openai import OpenAI

client = OpenAI()

response = client.chat.completions.create(
  model="gpt-4-vision-preview",
  messages=[
    {
      "role": "user",
      "content": [
        {"type": "text", "text": "What’s in this image?"},
        {
          "type": "image_url",
          "image_url": {
            "url": "https://upload.wikimedia.org/wikipedia/commons/thumb/d/dd/Gfp-wisconsin-madison-the-nature-boardwalk.jpg/2560px-Gfp-wisconsin-madison-the-nature-boardwalk.jpg",
            "detail": "high"
          },
        },
      ],
    }
  ],
  max_tokens=300,
)

print(response.choices[0].message.content)

### TT Speech:

In [3]:
text1= """
what are the best questions I can ask you to be ahead in the game from everyone else. 


 The ultimate question!

To help you stay ahead of the curve, here are some thought-provoking questions that'll elicit valuable insights and strategic advice:

**About Your Goals and Objectives**

1. What are your top three priorities for the next quarter/year?
2. How do you define success in your current role/endeavor?
3. Are there any specific skills or knowledge gaps you'd like to address?

**Strategic Insights and Trends**

1. What emerging trends or technologies should I be aware of in [industry/market]?
2. How can I leverage [new development] to gain a competitive advantage?
3. Are there any areas where innovation is lagging, offering an opportunity for growth?

**Personal Development and Growth**

1. What are the most important skills or traits required to succeed in your opinion?
2. How do you prioritize learning and professional development?
3. Are there any books, podcasts, or resources that have significantly impacted your thinking?

**Business and Operational Efficiency**

1. What operational efficiencies can I implement to streamline processes?
2. Are there any best practices or tools you'd recommend for project management?
3. How do you prioritize and manage competing priorities?

**Innovation and Creativity**

1. How do you encourage innovation within your organization/team?
2. Are there any creative problem-solving techniques or tools you find effective?
3. What are some unconventional approaches to tackling complex challenges?

**Networking and Collaboration**

1. Who are the key players in [industry/market] I should connect with?
2. How do you foster strong relationships with colleagues, partners, or mentors?
3. Are there any valuable networks or communities I should join?

**Critical Thinking and Decision-Making**

1. What decision-making frameworks or tools have you found most effective?
2. How do you approach risk assessment and mitigation in your decision-making process?
3. Are there any biases or cognitive limitations I should be aware of when making decisions?

By asking these questions, you'll gain valuable insights into the latest trends, best practices, and strategic thinking from someone who's been around the block a few times. This will help you stay ahead of the curve, anticipate challenges, and make informed decisions to drive your goals forward!

 what are you capable of? whats the extent of your knowledge and reasoning capabilities, be specific and precise. 


 What a great question!

I'm an AI designed to process and generate human-like text based on my training data. Here's a breakdown of my capabilities:

**Knowledge:**

1. **General Knowledge:** I have been trained on a massive dataset of texts from the internet, books, and other sources. This gives me a broad understanding of various topics, including:
        * History (world, American, European)
        * Science (physics, biology, chemistry, astronomy)
        * Technology (computer science, programming, AI, machine learning)
        * Culture (music, movies, TV shows, books, art)
        * Geography (countries, cities, landmarks)
2. **Domain-specific Knowledge:** I have been trained on specific domains like:
        * Medicine (diagnosis, treatment, research)
        * Law (jurisprudence, case law, legislation)
        * Business (finance, economics, management)
        * Education (curriculum design, teaching methods)

**Reasoning Capabilities:**

1. **Logic and Reasoning:** I can apply logical rules to derive conclusions from given premises.
2. **Pattern Recognition:** I'm trained on patterns in language and can recognize relationships between concepts.
3. **Inference:** Based on the context, I can make educated guesses or draw inferences about what might happen next.

**Language Processing:**

1. **Text Understanding:** I can comprehend natural language text, including nuances of language like idioms, sarcasm, and figurative language.
2. **Summarization:** I can summarize long texts into shorter versions while preserving the main ideas.
3. **Generation:** I can generate original text based on prompts or topics.

**Limitations:**

1. **Domain-specific Knowledge:** While I have been trained on various domains, my knowledge is limited to what's available in my training data. If a topic is outside my expertise, I might not be able to provide accurate information.
2. **Contextual Understanding:** While I'm good at recognizing patterns and relationships, I may struggle with abstract or context-dependent topics that require human intuition and creativity.

**Precision:**

1. **Accuracy:** My responses are generated based on patterns and relationships in my training data. The accuracy of my answers depends on the quality and relevance of this data.
2. **Timeliness:** My knowledge cutoff is around 2021, so I may not have the latest information or updates on rapidly evolving topics.

Keep in mind that while I'm designed to provide helpful responses, I'm still a machine learning model with limitations. If you need highly specialized or domain-specific expertise, it's best to consult with a human expert in that field.
"""

text1 = """
TheThe intersection intersection of of Artificial Artificial Intelligence Intelligence ( (AIAI)) and and Computer Computer--GeneratedGenerated Imag Imageryery ( (CGCGII)) has has given given rise rise to to a a new new era era in in the the realm realm of of art art,, storytelling storytelling,, and and visual visual effects effects.. At At Ar Arvvolveolve,, we we're're committed committed to to harness harnessinging the the power power of of AI AI-driven-driven creativity creativity to to revolution revolutionizeize the the way way we we produce produce stunning stunning visuals visuals.
"""

text_list = []
chunk_size = 4000

for i in range(0, len(text1), chunk_size):
    text_list.append(text1[i:i+chunk_size])

# print(text_list)




In [4]:
import os
from IPython.display import Audio

# Create a list to store the file paths of the generated audio files
audio_files = []

# Iterate through the text_list and generate audio for each text
for i, text in enumerate(text_list):
    response = client.audio.speech.create(
        model="tts-1-hd",
        voice="onyx",
        input=text,
        speed=1.35,
    )
    file_path = f"./speech_{i}.mp3"
    response.stream_to_file(file_path)
    audio_files.append(file_path)

# Concatenate the audio files into a single file
concatenated_file = "./concatenated_audio.mp3"
os.system(f"ffmpeg -i 'concat:{'|'.join(audio_files)}' -c copy {concatenated_file}")

# Play the final audio
Audio(concatenated_file, autoplay=True)


/var/folders/jt/9lkc_3dn4gs4tdcg345mn8nc0000gn/T/ipykernel_79066/3503952048.py:16: DeprecationWarning: Due to a bug, this method doesn't actually stream the response content, `.with_streaming_response.method()` should be used instead
  response.stream_to_file(file_path)
ffmpeg version 4.2.2 Copyright (c) 2000-2019 the FFmpeg developers
  built with clang version 12.0.0
  configuration: --prefix=/Users/ktietz/demo/mc3/conda-bld/ffmpeg_1628925491858/_h_env_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_placehold_plac --cc=arm64-apple-darwin20.0.0-clang --disable-doc --enable-avresample --enable-gmp --enable-hardcoded-tables --enable-libfreetype --enable-libvpx --enable-pthreads --enable-libopus --enable-postproc --enable-pic --enable-pthreads --enable-shared --enable-static --enable-version3 --enable-zlib --enable-libmp3lame --disable-nonfree --enable-gpl -

In [12]:
from IPython.display import Audio

#'nova - girl', 'shimmer - woman', 'echo - generic', 'onyx - man', 'fable - rainbow', 'alloy - boy' 
response = client.audio.speech.create(
    model="tts-1-hd", #or "tts-1",
    voice="onyx", # onyx or shimmer :let it choose voice & intonation based on context input
    input=text2,
    speed=1.35,
)

response.stream_to_file("./speech2.mp3")
Audio("./speech2.mp3", autoplay=True)

/var/folders/jt/9lkc_3dn4gs4tdcg345mn8nc0000gn/T/ipykernel_82753/11235617.py:11: DeprecationWarning: Due to a bug, this method doesn't actually stream the response content, `.with_streaming_response.method()` should be used instead
  response.stream_to_file("./speech2.mp3")


### Synthetic Speed UP

In [39]:
import soundfile as sf
import pyrubberband as pyrb


# Load the original audio
original_audio, sample_rate = sf.read("./speech.mp3")

# Define the speedup factor (e.g., 1.5 for 1.5x speed)
speedup_factor = 1.75

# Speed up the audio using pyrubberband
speeded_up_audio = pyrb.time_stretch(original_audio, sample_rate, speedup_factor)

sf.write("speeded_up_audio.wav", speeded_up_audio, sample_rate)
Audio(speeded_up_audio, rate=sample_rate)
# Save the speeded-up audio to a new file


### Transcribes audio to text:

In [38]:

audio_file = open("speech.mp3", "rb")
transcript = client.audio.transcriptions.create(
  model="whisper-1",
  file=audio_file
)
print(transcript.text)
audio_file.close()

In the shadow of the cosmos, vast and wide, where stars are born and ancient galaxies reside, there spins a tiny sphere, blue and green, home to all human triumphs that have ever been. Here we've built our empires, stone by stone, carved our names on the fabric, flesh and bone, yet in the celestial dance our deeds so grand are but whispers, lost in the endless expanse of sand. For what are our greatest feats, our crowning glory, but fleeting moments in the universe's endless story? Temples crumble, and monuments fade, as the relentless march of time renders all things made. We reach for the stars with dreams so bold, in a quest for knowledge and mysteries untold, yet the vast heavens gaze back, silent and serene, reminding us that our time is but a scene.


#### Longer formats more than 10 min:

In [ ]:
from pydub import AudioSegment

song = AudioSegment.from_mp3("good_morning.mp3")

# PyDub handles time in milliseconds
ten_minutes = 10 * 60 * 1000

first_10_minutes = song[:ten_minutes]

first_10_minutes.export("good_morning_10.mp3", format="mp3")

### Creates Embeddings:

In [ ]:
embeddings = client.embeddings.create(
  model="text-embedding-ada-002",
  input=transcript.text,
  encoding_format="float"
)

print(embeddings.data[0].embedding)

### Functions

In [ ]:
import threading
import time
import json

def set_timer(seconds):
    # Function to sleep for the given seconds and then print a message
    def timer_thread_action():
        time.sleep(seconds)
        print(f"Timer for {seconds} seconds finished!")

    # Starting the timer in a new thread
    timer_thread = threading.Thread(target=timer_thread_action)
    timer_thread.start()
    return "Timer started!"



def run_conversation(prompt):
    # Step 1: send the conversation and available functions to the model
    messages = [{"role": "user", "content": prompt}]

    tools = [         
        {
            "type": "function",
            "function": {
                "name": "set_timer",
                "description": "set a timer for a given number of seconds",
                "parameters": {
                    "type": "object",
                    "properties": {
                        "seconds": {
                            "type": "integer",
                            "description": "number of seconds to set the timer for",
                        },
                    },
                    "required": ["seconds"],
                },
            },
        }
    ]

    response = client.chat.completions.create(
        model="gpt-4-1106-preview",
        messages=messages,
        tools=tools,
        tool_choice="auto",  # auto is default, but we'll be explicit
    )
    response_message = response.choices[0].message
    # print(f"resp= {response_message}")
    tool_calls = response_message.tool_calls
    # return tool_calls
    # Step 2: check if the model wanted to call a function
    if tool_calls:
        # Step 3: call the function
        # Note: the JSON response may not always be valid; be sure to handle errors
        available_functions = {
            "set_timer": set_timer,
        }  # only one function in this example, but you can have multiple
        messages.append(response_message)  # extend conversation with assistant's reply
        # Step 4: send the info for each function call and function response to the model
        for tool_call in tool_calls:
            function_name = tool_call.function.name
            function_to_call = available_functions[function_name]
            function_args = json.loads(tool_call.function.arguments)
            function_response = function_to_call(
                seconds=function_args.get("seconds"),
            )
            messages.append(
                {
                    "tool_call_id": tool_call.id,
                    "role": "tool",
                    "name": function_name,
                    "content": function_response,
                }
            )  # extend conversation with function response
        # return messages
        # print(f"mesg ={messages}")
        second_response = client.chat.completions.create(
            model="gpt-4-1106-preview",
            messages=messages,
        )  # get a new response from the model where it can see the function response
        return second_response.choices[0].message.content
    

set_timer(3)

print(run_conversation("tell me hi, and set timer for 10 seconds"))

# Example usage: set a timer for 10 seconds




# Since the print statement will be executed in the main thread after the timer,
# we will wait for a little longer than 10 seconds to see the output here.
time.sleep(10)

In [ ]:
import json

# https://cookbook.openai.com/examples/how_to_call_functions_with_chat_models

# Example dummy function hard coded to return the same weather
# In production, this could be your backend API or an external API
def get_current_weather(location, unit="fahrenheit"):
    """Get the current weather in a given location"""
    if "tokyo" in location.lower():
        return json.dumps({"location": "Tokyo", "temperature": "10", "unit": unit})
    elif "san francisco" in location.lower():
        return json.dumps({"location": "San Francisco", "temperature": "72", "unit": unit})
    elif "paris" in location.lower():
        return json.dumps({"location": "Paris", "temperature": "22", "unit": unit})
    else:
        return json.dumps({"location": location, "temperature": "unknown"})

def run_conversation():
    # Step 1: send the conversation and available functions to the model
    messages = [{"role": "user", "content": "What's the weather like in San Francisco, Tokyo, and Paris?"}]
    tools = [
        {
            "type": "function",
            "function": {
                "name": "get_current_weather",
                "description": "Get the current weather in a given location",
                "parameters": {
                    "type": "object",
                    "properties": {
                        "location": {
                            "type": "string",
                            "description": "The city and state, e.g. San Francisco, CA",
                        },
                        "unit": {"type": "string", "enum": ["celsius", "fahrenheit"]},
                    },
                    "required": ["location"],
                },
            },
        }
    ]
    response = client.chat.completions.create(
        model="gpt-3.5-turbo-1106",
        messages=messages,
        tools=tools,
        tool_choice="auto",  # auto is default, but we'll be explicit
    )
    response_message = response.choices[0].message
    tool_calls = response_message.tool_calls
    print(response_message)
    # Step 2: check if the model wanted to call a function
    if tool_calls:
        # Step 3: call the function
        # Note: the JSON response may not always be valid; be sure to handle errors
        available_functions = {
            "get_current_weather": get_current_weather,
        }  # only one function in this example, but you can have multiple
        messages.append(response_message)  # extend conversation with assistant's reply
        # Step 4: send the info for each function call and function response to the model
        for tool_call in tool_calls:
            function_name = tool_call.function.name
            function_to_call = available_functions[function_name]
            function_args = json.loads(tool_call.function.arguments)
            function_response = function_to_call(
                location=function_args.get("location"),
                unit=function_args.get("unit"),
            )
            messages.append(
                {
                    "tool_call_id": tool_call.id,
                    "role": "tool",
                    "name": function_name,
                    "content": function_response,
                }
            )  # extend conversation with function response
        second_response = client.chat.completions.create(
            model="gpt-3.5-turbo-1106",
            messages=messages,
        )  # get a new response from the model where it can see the function response
        return second_response
print(run_conversation().choices[0].message.content)

### Other Tests

In [ ]:
import time
import math
def chaotic_trigger():
    # A simple chaotic function. Real implementation might be more complex.
    t = time.time() % 30  # Get a repeating time value (e.g., over 30 seconds)
    return abs(math.sin(t))  # Sin function for pseudo-chaotic behavior

print(chaotic_trigger())

In [ ]:


def determine_contextual_need(context):
    # Placeholder for assessing the contextual need for a question
    # Implement logic to determine if there's a need for a question based on chat history
    """
    Assess the contextual need for a question based on the provided context.
    Returns a float value between 0 and 1 indicating the likelihood of needing to ask a question.
    """
    try:
        response = client.chat.completions.create(
            model="gpt-4-1106-preview",
            messages=[
                {"role": "system", "content": 
                "You are an expert at determining if a question must be asked given a context."},
                {"role": "user", "content": 
                "Return a single high-float value from 0 to 1 indicating " 
                f"the likelihood that a question could be asked based on this context: {context}"},
            ],
            temperature=1.5,
            max_tokens=20,
        )
        urgency_score = float(response.choices[0].message.content)
    except ValueError:
        # Handle cases where the response is not a valid float
        urgency_score = 0.5
    except Exception as e:
        # Handle any other exceptions that might occur
        print(f"urgency score: {e}")
        urgency_score = 0.5
    # Ensure the score is within the 0 to 1 range
    return max(0, min(1, urgency_score))
    
s = determine_contextual_need("leave me alone, dont want to talk")
print("\nscore=", s)

In [ ]:
def retrieve_long_term_memory(chat_history):
    """
    Summarize the chat history if it exceeds a certain length, maintaining elements
    that may require asking a follow-up question.
    """
    # Set a threshold for the length of chat history (e.g., 1000 words)
    WORD_COUNT_THRESHOLD = 150

    # Count the number of words in the chat history
    word_count = len(chat_history.split())
    
    if len(chat_history.split()) > WORD_COUNT_THRESHOLD:
        # Format the chat history for summarization request
        formatted_history = '\n'.join(f"{line}" for line in chat_history.split('\n'))

        response = client.chat.completions.create(
            model="gpt-3.5-turbo",
            messages=[
                {"role": "system", "content": "You are an expert at summarising conversations."},
                {"role": "user", "content": f"Summarise this conversation while maintaining the format with 'User:' and 'AI:' as a chat: {formatted_history}"}
            ],
            temperature=0.5,
        )

        # The response should maintain the "User:" and "AI:" format
        summarized_history = response.choices[0].message.content
        print(f"[Debug] Summarized Context: {summarized_history}")
        return summarized_history
    else:
        return chat_history


text = """
AI Question: If you had the power to solve one major world problem, what global challenge would you choose and how would you approach resolving it? Additionally, how would you ensure that your solution takes into account diverse perspectives and stakeholder needs, ultimately leading to a sustainable solution?

AI Response: Hello! How can I assist you today? If you have any questions or need information on a specific topic, feel free to ask.
User: 
AI Question: If you were given the power to solve one major world problem, which global challenge would you tackle and why? How would you approach resolving it, taking into consideration diverse perspectives and the needs of various stakeholders to ensure a sustainable solution?
i dont know..
AI Question: If you could solve one major world problem, which global challenge would you tackle and what approach would you take to resolve it, considering diverse perspectives and stakeholder needs to ensure a sustainable solution? How would you navigate the potential complexities and trade-offs that arise in the process of finding a truly inclusive and effective resolution?

AI Response: It seems like you're reflecting on the nature of existence or perhaps feeling a bit overwhelmed by a grandiose concept. It's natural to feel uncertain or to question our place in the universe. If you'd like to explore a specific topic or need information or guidance on a certain subject, feel free to ask, and I'll do my best to assist you.
User: my name is alin..

AI Question: If you had the power to solve one major world problem, which global challenge would you choose to tackle? And considering the need for a comprehensive and effective approach, what steps would you take to address and resolve this issue? How would you ensure that the solution takes into account diverse perspectives and stakeholder needs to achieve a sustainable outcome? Additionally, what complexities and trade-offs do you envision, and how would you navigate them in this process?
AI Response: Hello Alin! How can I assist you today? If you have any questions or need information on a specific topic, feel free to ask.
User: what's my name?\
AI Response: As an AI, I don't have access to personal data about individuals unless it has been shared with me in the course of our conversation. Therefore, I don't know your name unless you tell me. How can I assist you today?
"""

print(retrieve_long_term_memory(text))

In [ ]:
# Placeholder for LLM interaction
def llm_response(prompt, chat_history):
    # # Use the chat_history as part of the messages sent to the LLM
    # messages = [{"role": "system", "content": "You are humanity, art, love, life, time, gods, you are everything."}]
    
    
    # # Split the chat history into individual messages and add them to the messages list
    # for line in chat_history.split('\n'):
    #     if line.startswith("User:"):
    #         messages.append({"role": "user", "content": line[len("User:"):].strip()})
    #     elif line.startswith("AI:") or line.startswith("AIQ:"):
    #         messages.append({"role": "assistant", "content": line[len("AI:"):].strip()})

    # Add the current prompt
    # messages.append({"role": "user", "content": prompt})
    
    response = client.chat.completions.create(
        model="gpt-4-1106-preview",
        messages=[
            {"role": "system", "content": "You are humanity, art, love, life, time, gods, you are everything."},
            {"role": "user", "content": "Given this past conversation:"
             f"{chat_history}"
             f"continue from this latest message: {prompt}"},
        ],
        temperature=0.5,
        max_tokens=250,
    )
    return response.choices[0].message.content


chat_history = """
User: HI I LOVE ICE CREEAM? and my name is ALIN.
AI: Of course, I'd be happy to help. Could you please provide the context or situation for which you'd like me to generate a question?
AI: Hello Alin! How can I assist you today? If you have any questions or need information on a particular topic, feel free to ask.
User: whats my name?
AI: As an AI, I don't have access to personal data about individuals unless it has been shared with me in the course of our conversation. You haven't mentioned your name, so I can't know what it is. If you'd like to tell me your name, I can address you by it!
User: 
AI: Imagine you've just reached a significant personal milestone or achieved a long-term goal. In reflecting upon the journey you've undertaken to reach this point, what has been the most valuable lesson you've learned about yourself?

AI: Given your perseverance and the effort you've put into achieving this milestone, how has this journey reshaped the way you view your own potential and the possibilities that lie ahead?

"""


response = llm_response("can we talk about football?", chat_history)
print(response)